In [ ]:
from IPython.display import clear_output 

!pip install transformers==4.8.2
!pip install sentencepiece==0.1.96
!pip install tensorflow_addons

clear_output()

In [ ]:
import sklearn
import tensorflow
import transformers
import tensorflow_addons

print(sklearn.__version__) # 1.0.2
print(tensorflow.__version__) # 2.8.0
print(transformers.__version__) # 4.8.2
print(tensorflow_addons.__version__) # 0.16.1

import sentencepiece

1.0.2
2.8.0
4.8.2
0.17.0


In [ ]:
import pandas as pd
import numpy as np

import os
import re
import pickle 
import dill # for saving a function as a file(.pkl)
import logging # for changing the tf's logging level
import urllib.request
from tqdm import tqdm

from sklearn import model_selection
from sklearn.metrics import accuracy_score

import tensorflow as tf
import tensorflow_addons as tfa # for using Rectified-Adam optimizer (instead of Adam optimizer) 
from tensorflow.keras import layers, initializers, losses, optimizers, metrics, callbacks 

import transformers
from transformers import TFBertModel # BertTokenizer 제외

import sentencepiece as spm

In [ ]:
# Random seed 고정
tf.random.set_seed(1234)
np.random.seed(1234)

# Transformers logging level 변경 (WARNING -> ERROR) @ https://huggingface.co/transformers/main_classes/logging.html
transformers.logging.set_verbosity(transformers.logging.ERROR)

# Tensorflow logging level 변경 
tf.get_logger().setLevel(logging.ERROR)

# load data

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
df=pd.read_csv("/content/drive/MyDrive/final (1)/new_train_with_neu.csv",index_col=0)

In [ ]:
df

index                                           Sentence label
0           1               아 진짜! 사무실에서 피지 말라니깐! 간접흡연이 얼마나 안좋은데!    분노
1           2       그럼 직접흡연하는 난 얼마나 안좋겠니? 안그래? 보면 꼭... 지 생각만 하고.    혐오
2           3                                            손님 왔어요.    중립
3           4                                            손님? 누구?    중립
4           5                                     몰라요. 팀장님 친구래요.    중립
...       ...                                                ...   ...
113563  38589               솔직히 예보 제대로 못하는 데 세금이라도 아끼게 그냥 폐지해라..    혐오
113564  38590                                        재미가 없으니 망하지    혐오
113565  38591  공장 도시락 비우생적임 아르바이트했는데 화장실가성 손도 않씯고 재료 담고 바닥 떨어...    혐오
113566  38592               코딱지 만한 나라에서 지들끼리 피터지게 싸우는 센징 클래스 ㅉㅉㅉ    혐오
113567  38593               와이프도 그렇고 댓글 다 볼텐데 이휘재 좀 하차 하라고 전해주세요    혐오

[113568 rows x 3 columns]

In [ ]:
df[ df['Sentence'].duplicated(keep=False) == True ].sort_values('Sentence')

index                            Sentence label
240      241   ... 그래. 알았어. 그만 하자. 내가 잘못했어. 그만해.    슬픔
2969    2973   ... 그래. 알았어. 그만 하자. 내가 잘못했어. 그만해.    슬픔
39        40     ... 너 오늘 유난히 대답 잘 한다? 라임 맞춰가면서.    혐오
2768    2772     ... 너 오늘 유난히 대답 잘 한다? 라임 맞춰가면서.    혐오
2806    2810                         ... 화장실 가지.    중립
...      ...                                 ...   ...
6589    6594                                  흠…    중립
16608  16613                                 흥..    중립
4609    4614                                 흥..    중립
7827    7832                                 히잉…    슬픔
21902  21907                                 히잉…    중립

[10116 rows x 3 columns]

In [ ]:
df["label"].value_counts()

중립    51869
분노    12556
놀람    12519
행복    11615
슬픔    10087
혐오     7970
공포     6952
Name: label, dtype: int64

In [ ]:
df = df.drop_duplicates('Sentence') 
df = df.reset_index(drop=True)

In [ ]:
df["label"].value_counts()

중립    48282
분노    12086
놀람    11223
행복    10623
슬픔     9319
혐오     7572
공포     6707
Name: label, dtype: int64

In [ ]:
print('중복 제거 후 전체 리뷰 수 :', len(df))

중복 제거 후 전체 리뷰 수 : 105812


In [ ]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 105812 entries, 0 to 105811
Data columns (total 3 columns):
 #   Column    Non-Null Count   Dtype 
---  ------    --------------   ----- 
 0   index     105812 non-null  int64 
 1   Sentence  105812 non-null  object
 2   label     105812 non-null  object
dtypes: int64(1), object(2)
memory usage: 2.4+ MB


In [ ]:
del df["index"]

Undersampling


In [ ]:
df_mid=df[df["label"] == "중립"]
df_not_mid=df[df["label"] != "중립"]

In [ ]:
df_mid

Sentence label
2                                        손님 왔어요.    중립
3                                        손님? 누구?    중립
4                                 몰라요. 팀장님 친구래요.    중립
5                                   내 친구? 친구 누구?    중립
7                                 그래서... 무슨 일 해?    중립
...                                          ...   ...
94381                    호텔 CCTV ,차량 블랙박스 조사해보세요    중립
94382  ㅋㅋㅋㅋ 어제 누가 헬쥐졌으니 3시에 올라올거라 하더니 4시....ㅋㅋㅋㅋ    중립
94383                     공격에선 체력저하로 세컨볼 획득 안됨..    중립
94384                   한화가 삼성과 KT는 기본으로 깔고 가겠네.    중립
94385             실제 저런몸이 오히려 대한민국 여자들에게 인기가 많다.    중립

[48282 rows x 2 columns]

In [ ]:
df_not_mid

Sentence label
0                    아 진짜! 사무실에서 피지 말라니깐! 간접흡연이 얼마나 안좋은데!    분노
1            그럼 직접흡연하는 난 얼마나 안좋겠니? 안그래? 보면 꼭... 지 생각만 하고.    혐오
6                                          그걸 내가 어떻게 알아요!    분노
14                                   동사무소에서 인구조사 나왔니? 지금.    분노
16                                        나? ... 나보고 하라고?    놀람
...                                                   ...   ...
105807               솔직히 예보 제대로 못하는 데 세금이라도 아끼게 그냥 폐지해라..    혐오
105808                                        재미가 없으니 망하지    혐오
105809  공장 도시락 비우생적임 아르바이트했는데 화장실가성 손도 않씯고 재료 담고 바닥 떨어...    혐오
105810               코딱지 만한 나라에서 지들끼리 피터지게 싸우는 센징 클래스 ㅉㅉㅉ    혐오
105811               와이프도 그렇고 댓글 다 볼텐데 이휘재 좀 하차 하라고 전해주세요    혐오

[57530 rows x 2 columns]

In [ ]:
# random undersampling
df_mid=df_mid.sample(frac=0.25,random_state=1004)

In [ ]:
df=pd.concat([df_mid,df_not_mid])

In [ ]:
df

Sentence label
37107                                         오늘 접대가 있어서~    중립
93748                                 케바케 오십년전에도 쓰던 말인데..    중립
24018                                              할망구같아.    중립
91429                   이거 해결 안되면 삼성은 큰 위기에 빠질 것은 불보듯 뻔하다    중립
65558                           나 오늘 짭새새끼들이 몰려있길래 구경갔다왔다.    중립
...                                                   ...   ...
105807               솔직히 예보 제대로 못하는 데 세금이라도 아끼게 그냥 폐지해라..    혐오
105808                                        재미가 없으니 망하지    혐오
105809  공장 도시락 비우생적임 아르바이트했는데 화장실가성 손도 않씯고 재료 담고 바닥 떨어...    혐오
105810               코딱지 만한 나라에서 지들끼리 피터지게 싸우는 센징 클래스 ㅉㅉㅉ    혐오
105811               와이프도 그렇고 댓글 다 볼텐데 이휘재 좀 하차 하라고 전해주세요    혐오

[69600 rows x 2 columns]

In [ ]:
df.value_counts(["label"])

label
분노       12086
중립       12070
놀람       11223
행복       10623
슬픔        9319
혐오        7572
공포        6707
dtype: int64

In [ ]:
emotion_mapping = {"분노":0,"중립":1, "놀람":2, "행복":3, "슬픔":4, "혐오":5,"공포":6 }

df['label'] = df['label'].map(emotion_mapping)

In [ ]:
df.value_counts(["label"])

label
0        12086
1        12070
2        11223
3        10623
4         9319
5         7572
6         6707
dtype: int64

In [ ]:
train_x, test_x, train_y, test_y = model_selection.train_test_split(df['Sentence'], df['label'], 
                                                                    test_size=0.3, 
                                                                    random_state=42) 

# preprocessing

In [ ]:
#KoBERT 불러오기
!git clone https://github.com/monologg/KoBERT-Transformers.git
!mv KoBERT-Transformers/kobert_transformers/tokenization_kobert.py /content
clear_output() # clear the output

#토크나이저 생성
from tokenization_kobert import KoBertTokenizer 

tokenizer = KoBertTokenizer.from_pretrained('monologg/kobert')

In [ ]:
df['Sentence'].str.len().sort_values(ascending=False)[:5]

81102     299
99490     298
105387    295
103808    261
39088     209
Name: Sentence, dtype: int64

In [ ]:
len(tokenizer.tokenize(df['Sentence'][81102]))

75

In [ ]:
df['Sentence'][81102]

'쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기'

In [ ]:
len(tokenizer.tokenize(df['Sentence'][99490]))

292

In [ ]:
len(tokenizer.tokenize(df['Sentence'][105387]))

188

In [ ]:
SEQ_LEN = 300

token_ids = []
token_segments = []
token_masks = []

train_labels = []

for idx in tqdm(range(len(train_x))):

  # 'Sentence'칼럼에서 0번째 행~ 꺼내오기
  train_sentence = train_x.iloc[idx]
  print(train_sentence) 

  # 특수문자 제거
  cleaned_sentence = re.sub("[^\s0-9a-zA-Zㄱ-ㅎㅏ-ㅣ가-힣]", "", train_sentence)
  print(cleaned_sentence)

  # 토큰화 + 토큰별 시퀀스번호 부여 + 패딩
  encoded_dict = tokenizer.encode_plus(text = cleaned_sentence,
                                       padding='max_length',
                                       truncation=True,
                                       max_length=SEQ_LEN
                                       )
  
  #'input_ids', 'token_type_ids', 'attention_mask'
  token_ids.append(encoded_dict['input_ids'])
  token_masks.append(encoded_dict['attention_mask'])
  token_segments.append(encoded_dict['token_type_ids'])

  train_labels.append(train_y.iloc[idx])


train_inputs = (np.array(token_ids), np.array(token_masks), np.array(token_segments))
train_labels = np.array(train_labels)

  1%|          | 247/48720 [00:00<00:19, 2461.75it/s]

이민호 눈물연기 대박 ㅠ ㅠㅠ
이민호 눈물연기 대박 ㅠ ㅠㅠ
곰팡이 제거제가 효과가 있어?
곰팡이 제거제가 효과가 있어
죄다 틀딱이냐 무슨 ㅋㅋㅋㅋㅋㅋㅋㅋㅋ
죄다 틀딱이냐 무슨 ㅋㅋㅋㅋㅋㅋㅋㅋㅋ
대통령께 죄송한 마음 뿐입니다
대통령께 죄송한 마음 뿐입니다
실수 계속 하고 눈치 보는거 당연한건가요???
실수 계속 하고 눈치 보는거 당연한건가요
누군가 싸우는지 시끄럽고 난리도 아니야. 사람도 많고.
누군가 싸우는지 시끄럽고 난리도 아니야 사람도 많고
그거 참 좋은 생각인걸.
그거 참 좋은 생각인걸
심청아 올시험도 불합격했으니 한강에 인신공양 하러 가자ㅠㅠ
심청아 올시험도 불합격했으니 한강에 인신공양 하러 가자ㅠㅠ
 깜깜한 암흑의 공간인줄 알았는데 빛나는 수많은 별들이 반짝거리고 있더라고요.
 깜깜한 암흑의 공간인줄 알았는데 빛나는 수많은 별들이 반짝거리고 있더라고요
그런 괴롭힘, 좋지 않다고 봐. 자, 가 볼까…….
그런 괴롭힘 좋지 않다고 봐 자 가 볼까
13연승 압도적인데 ..
13연승 압도적인데 
어떻게 극복해야 할까요
어떻게 극복해야 할까요
근혜야 국민연금이 니꺼냐
근혜야 국민연금이 니꺼냐
소송비가 더 나오지 않나여
소송비가 더 나오지 않나여
미국놈들은 지들도 국경 붙어있는 나라랑 화합도 못하면서 우리한텐 일본이랑 사이좋게 지내라고 하네 ㅋㅋㅋㅋㅋㅋ
미국놈들은 지들도 국경 붙어있는 나라랑 화합도 못하면서 우리한텐 일본이랑 사이좋게 지내라고 하네 ㅋㅋㅋㅋㅋㅋ
그냥. 이번에 삼성 엄청 오르락 내리락 하잖아. 그래서 삼성 한 번 들어 봤지.
그냥 이번에 삼성 엄청 오르락 내리락 하잖아 그래서 삼성 한 번 들어 봤지
비상벨 눌렀는데 그래도 지금 너무 무서워.
비상벨 눌렀는데 그래도 지금 너무 무서워
머리 하느라 구조를 못한게 아니다..애초에 구조할 맘이 1도 없었기 때문에 머리 할 여유가 있었던거다..그게 더 무섭다...
머리 하느라 구조를 못한게 아니다애초에 구조할 맘이 1도 없었기 때문에 머리 할 여유가 있었던거다그게 더 무섭다
그래야겠다. 빨리 전화부터 해야

  1%|          | 494/48720 [00:00<01:17, 626.20it/s] 

그런 것 같아. 우리 집엔 창문도 없어.
그런 것 같아 우리 집엔 창문도 없어
너무나 통탄할 일이다.
너무나 통탄할 일이다
가, 이자식아!!
가 이자식아
내가 너무나 좋아하는 인플루언서가 있는데, 인플루언서가 진행하는 이벤트에 당첨 된 거야!
내가 너무나 좋아하는 인플루언서가 있는데 인플루언서가 진행하는 이벤트에 당첨 된 거야
당첨 선물이 내가 좋아하는 향수라서 너무나 마음에 들어.
당첨 선물이 내가 좋아하는 향수라서 너무나 마음에 들어
티비조선 슬슬 편집하네
티비조선 슬슬 편집하네
너무너무 올려줘서 고마워요ㅜㅜㅜ
너무너무 올려줘서 고마워요ㅜㅜㅜ
에? 바이킹이요?
에 바이킹이요
나 가상현실기 사성 해봤는댕 헉 걍 애들 장남검수준 별로 몰입도 않돼긍 속았단 느낌 들더라구
나 가상현실기 사성 해봤는댕 헉 걍 애들 장남검수준 별로 몰입도 않돼긍 속았단 느낌 들더라구
저돈은 어디서 나온걸까...ㅡㅡ
저돈은 어디서 나온걸까ㅡㅡ
그러면 지금 상태도 며칠 만에 다 괜찮아질 수는 없는 거죠?
그러면 지금 상태도 며칠 만에 다 괜찮아질 수는 없는 거죠
아 왜이래 아빠! 가! 쫌!
아 왜이래 아빠 가 쫌
아들군대 안보낼려고 목숨거는구나
아들군대 안보낼려고 목숨거는구나
돌에 맞아 죽어라
돌에 맞아 죽어라
코피나면 치료를해야죠 어디봐요.
코피나면 치료를해야죠 어디봐요
그렇지 않아도 우리 신랑이 사진 찍어 놨어.
그렇지 않아도 우리 신랑이 사진 찍어 놨어
주위에 사람들은 싸움이 나서 그렇다는데 난 정확하게 보지 못했어.
주위에 사람들은 싸움이 나서 그렇다는데 난 정확하게 보지 못했어
트럼프 되면 전쟁날거같긴 함..
트럼프 되면 전쟁날거같긴 함
 그저 보고싶어죽겟어요
 그저 보고싶어죽겟어요
코로나로 못나가서 우울해.
코로나로 못나가서 우울해
코로나때문에 재택근무를 시작하면서 집 안에만 있으니까 마음이 울적해졌어.
코로나때문에 재택근무를 시작하면서 집 안에만 있으니까 마음이 울적해졌어
맞아. 존버는 승리한다.
맞아 존버는 승리한다
음악을 들으면 우울한 마음이 좀 가라앉을 수 있을까?
음

  2%|▏         | 851/48720 [00:00<00:46, 1031.89it/s]

...


사진 찍어두라고 왜 사진 그냥 찍어둬볼까
여기 건너편 상가 게임방인데요. 냉면 좀 갖다 주세요.
여기 건너편 상가 게임방인데요 냉면 좀 갖다 주세요
상황 봐서 손해 보더라고 팔아야겠지.
상황 봐서 손해 보더라고 팔아야겠지
제 운도 여기까지 인듯ㅠㅠ
제 운도 여기까지 인듯ㅠㅠ
절망그자체다..
절망그자체다
진짜 너무 힘들어요이건 그냥 잘생겨서...
진짜 너무 힘들어요이건 그냥 잘생겨서
그... 그건...
그 그건
어? 무, 물 좀 마시려고.
어 무 물 좀 마시려고
원래. 시보는 일주일에 한번 나오는 거잖아!!
원래 시보는 일주일에 한번 나오는 거잖아
응 봄에서 여름만 심한거 잘 알고있어~~
응 봄에서 여름만 심한거 잘 알고있어
일단 말투가 서서히 차가워짐
일단 말투가 서서히 차가워짐
다른 뮤지션과 함동공연이라서 형대가 피날레일 줄은 몰랐어요. ^^(댓글로)
다른 뮤지션과 함동공연이라서 형대가 피날레일 줄은 몰랐어요 댓글로
당첨 선물이 내가 예전부터 갖고 싶었던 거라서 너무나 마음에 들어.
당첨 선물이 내가 예전부터 갖고 싶었던 거라서 너무나 마음에 들어
가지고 싶던 거였어.
가지고 싶던 거였어
용건은 뭔데?
용건은 뭔데
역시 성룡이야 ㅋㅋㅋㅋㅋㅋㅋㅋ
역시 성룡이야 ㅋㅋㅋㅋㅋㅋㅋㅋ
박사모 쓰래기들아 ㅛ거 처ㅡ무라 ㅋㅋ요런 ㄱ ㅐ 쓰래기들 ㅇ ㅏ
박사모 쓰래기들아 ㅛ거 처ㅡ무라 ㅋㅋ요런 ㄱ ㅐ 쓰래기들 ㅇ ㅏ
박근혜는 도대체 얼마나 강심장인거야..
박근혜는 도대체 얼마나 강심장인거야
야구장갈 계획 없다.
야구장갈 계획 없다
아! 이거 뭐 말해야겠지?
아 이거 뭐 말해야겠지
인간 쓰레기 박지원 같은 색기들이 왜 이렇게 많으냐
인간 쓰레기 박지원 같은 색기들이 왜 이렇게 많으냐
그 특유의 유쾌함이 참 팀에 많은 도움을 준다. 고마워요~
그 특유의 유쾌함이 참 팀에 많은 도움을 준다 고마워요
형!!
형
국제정세가 우리나라 정신바짝차리지않으면 안더겠다
국제정세가 우리나라 정신바짝차리지않으면 안더겠다
개돼지는 이제 밖에 나가서도 처맞습니다 꿀꿀 ㅋ
개돼지는 이제 밖에 나가서

 99%|█████████▉| 48348/48720 [00:48<00:00, 1094.86it/s]


잠깐만
근데 진짜 내려오면 누가해요
근데 진짜 내려오면 누가해요
예에... 아무도 없어서...
예에 아무도 없어서
나라는 존재가 생각이나 날까?
나라는 존재가 생각이나 날까
너무 이러지 말자. 내가 진짜 제대로 당신 한번 호강시켜준다.
너무 이러지 말자 내가 진짜 제대로 당신 한번 호강시켜준다
지금까지 집계한 바로는, 예상했던 거 이상으로 결과들이 좋던데?
지금까지 집계한 바로는 예상했던 거 이상으로 결과들이 좋던데
흑돌이가 복이 많다
흑돌이가 복이 많다
난 오빠가 너무 좋은데...너무 좋은데...
난 오빠가 너무 좋은데너무 좋은데
헐 Wham 듀오때부터 좋아했는데 좀 충격 고인의 명복을 빕니다
헐 Wham 듀오때부터 좋아했는데 좀 충격 고인의 명복을 빕니다
시진핑하고 아베 김정은이 요세놈이 제일문제네.
시진핑하고 아베 김정은이 요세놈이 제일문제네
근데 이거 오피셜되면 진짜 엘지구단이 미친거 아닌가..
근데 이거 오피셜되면 진짜 엘지구단이 미친거 아닌가
짜고 치는 고스돕! 뻥 좀 작작 쳐라!진실은 곧 드러나기 마련이다.
짜고 치는 고스돕 뻥 좀 작작 쳐라진실은 곧 드러나기 마련이다
단일경기 최다득점 오늘로써 1위 바뀌었슴요...골스가 149점..ㅎㄷㄷ
단일경기 최다득점 오늘로써 1위 바뀌었슴요골스가 149점ㅎㄷㄷ
 미국 가면 이런 몸매 콤플렉스를 제가 조금이라도 떨칠수있을까요ㅠㅠ
 미국 가면 이런 몸매 콤플렉스를 제가 조금이라도 떨칠수있을까요ㅠㅠ
광화문 너무 춥네용
광화문 너무 춥네용
대단하네 수고했어요 축하합니다
대단하네 수고했어요 축하합니다
내가 10km 마라톤 대회에 출전했는데 이전의 내 기록을 갱신했어. 너무 기분이 좋아.
내가 10km 마라톤 대회에 출전했는데 이전의 내 기록을 갱신했어 너무 기분이 좋아
아니 요즘은 다들 왜그러지? 이해가 안가네.
아니 요즘은 다들 왜그러지 이해가 안가네
어 이게 무슨 냄새야?
어 이게 무슨 냄새야
부모 잘만나 호강하는구나...
부모 잘만나 호강하는구나
네, 필요하시면 가져가세요.
네 필요하시면 가져가세요
너만 빠지

100%|██████████| 48720/48720 [00:49<00:00, 986.47it/s]

다음 생애 의자왕이 되겠다는 거네
올랜도 개크던데...
올랜도 개크던데
그래서 평소에 안 그러던 애가 그러니까 이상하잖아. 너, 용돈 올려 달라고 그러는 거지?
그래서 평소에 안 그러던 애가 그러니까 이상하잖아 너 용돈 올려 달라고 그러는 거지
나도 눈물 펑펑..ㅜㅠ
나도 눈물 펑펑ㅜㅠ
그래. 얼마나 도대체 계속 이렇게 집 안에 있어야 될까.
그래 얼마나 도대체 계속 이렇게 집 안에 있어야 될까
누나 일이나 신경 써! 병원 일에 누나가 왜 껴들어? 내가 애야?
누나 일이나 신경 써 병원 일에 누나가 왜 껴들어 내가 애야
아닙니다. 꼭 뛰고 싶습니다! 전 세계 최고의 마라토너가 되기 위해서 태어났다고 아버지가 늘 말씀하셨는데... 하여튼, 죽어두 뛰다 죽겠습니다. 
아닙니다 꼭 뛰고 싶습니다 전 세계 최고의 마라토너가 되기 위해서 태어났다고 아버지가 늘 말씀하셨는데 하여튼 죽어두 뛰다 죽겠습니다 
드디어 가을야구가 현실이되었구나!
드디어 가을야구가 현실이되었구나
제가너무 발끈하는걸까요?.....
제가너무 발끈하는걸까요
 제대하고 처음사귄여자는 제대한 남자가 여자 갖고 놀려는 심보로만나는거다 ㅠㅠ
 제대하고 처음사귄여자는 제대한 남자가 여자 갖고 놀려는 심보로만나는거다 ㅠㅠ
저거저거 저게 인간이냐?
저거저거 저게 인간이냐
조금 더 지켜보면 주가가 오를까? 너무 걱정이 돼.
조금 더 지켜보면 주가가 오를까 너무 걱정이 돼
종목이 뭔지 모르고 그냥 아는 사람이 가르쳐줬어.
종목이 뭔지 모르고 그냥 아는 사람이 가르쳐줬어
쓰레기통에서 역겨운 냄새가 나고 있어. 어떡하지?
쓰레기통에서 역겨운 냄새가 나고 있어 어떡하지
그래. 구매할게. 좋은 거 있으면 추천해 줘.
그래 구매할게 좋은 거 있으면 추천해 줘
삼성 망한다고 개인이 망하냐?
삼성 망한다고 개인이 망하냐
아! 좋은 생각이 났어요. 자, 여기. 교수실 열쇠에요. 구석에 제가 밤샐 때 쓰는 침낭이랑 난로도 있으니까 찜질방보다 나을거예요.
아 좋은 생각이 났어요 자 여기 교수실 열쇠에요 구석에 제가 밤샐 때 쓰는 침낭

In [ ]:
train_inputs

(array([[   2, 3695, 7925, ...,    1,    1,    1],
        [   2,  517, 5449, ...,    1,    1,    1],
        [   2, 4212, 5782, ...,    1,    1,    1],
        ...,
        [   2, 4102, 2149, ...,    1,    1,    1],
        [   2, 1205, 5760, ...,    1,    1,    1],
        [   2, 3990, 6022, ...,    1,    1,    1]]),
 array([[1, 1, 1, ..., 0, 0, 0],
        [1, 1, 1, ..., 0, 0, 0],
        [1, 1, 1, ..., 0, 0, 0],
        ...,
        [1, 1, 1, ..., 0, 0, 0],
        [1, 1, 1, ..., 0, 0, 0],
        [1, 1, 1, ..., 0, 0, 0]]),
 array([[0, 0, 0, ..., 0, 0, 0],
        [0, 0, 0, ..., 0, 0, 0],
        [0, 0, 0, ..., 0, 0, 0],
        ...,
        [0, 0, 0, ..., 0, 0, 0],
        [0, 0, 0, ..., 0, 0, 0],
        [0, 0, 0, ..., 0, 0, 0]]))

In [ ]:
train_labels

array([3, 0, 0, ..., 4, 1, 0])

# modeling

In [ ]:
def create_model(max_length=300):

    bert_base_model = TFBertModel.from_pretrained("monologg/kobert", from_pt=True) 

    input_token_ids   = layers.Input((max_length,), dtype=tf.int32, name='input_token_ids')   # tokens_tensor
    input_masks       = layers.Input((max_length,), dtype=tf.int32, name='input_masks')       # masks_tensor
    input_segments    = layers.Input((max_length,), dtype=tf.int32, name='input_segments')    # segments_tensor  

    bert_outputs = bert_base_model([input_token_ids, input_masks, input_segments]) 
    

    bert_outputs = bert_outputs[1] # ('pooler_output', <KerasTensor: shape=(None, 768) dtype=float32 (created by layer 'tf_bert_model')>)
    bert_outputs = layers.Dropout(0.2)(bert_outputs)
    final_output = layers.Dense(units=7, activation='softmax', kernel_initializer=initializers.TruncatedNormal(stddev=0.02), name="classifier")(bert_outputs)

    model = tf.keras.Model(inputs=[input_token_ids, input_masks, input_segments], 
                        outputs=final_output)

    model.compile(optimizer=tfa.optimizers.RectifiedAdam(learning_rate=1e-5, weight_decay=0.0025, warmup_proportion=0.05),
                  loss=losses.SparseCategoricalCrossentropy(), 
                  metrics=[metrics.SparseCategoricalAccuracy()])
    
    return model

In [ ]:
# TPU setting

resolver = tf.distribute.cluster_resolver.TPUClusterResolver(tpu='grpc://' + os.environ['COLAB_TPU_ADDR'])
tf.config.experimental_connect_to_cluster(resolver)
tf.tpu.experimental.initialize_tpu_system(resolver)
print("\nAll devices: ", tf.config.list_logical_devices('TPU'))

strategy = tf.distribute.TPUStrategy(resolver)

with strategy.scope(): 
    model = create_model(max_length=300)


All devices:  [LogicalDevice(name='/job:worker/replica:0/task:0/device:TPU:0', device_type='TPU'), LogicalDevice(name='/job:worker/replica:0/task:0/device:TPU:1', device_type='TPU'), LogicalDevice(name='/job:worker/replica:0/task:0/device:TPU:2', device_type='TPU'), LogicalDevice(name='/job:worker/replica:0/task:0/device:TPU:3', device_type='TPU'), LogicalDevice(name='/job:worker/replica:0/task:0/device:TPU:4', device_type='TPU'), LogicalDevice(name='/job:worker/replica:0/task:0/device:TPU:5', device_type='TPU'), LogicalDevice(name='/job:worker/replica:0/task:0/device:TPU:6', device_type='TPU'), LogicalDevice(name='/job:worker/replica:0/task:0/device:TPU:7', device_type='TPU')]


# Train

In [ ]:
# Checkpoint setting for saving the best model
from google.colab import drive
drive.mount('/gdrive')

checkpoint_path = '/gdrive/MyDrive/final/colab_data/saved_models/'

if not os.path.exists(checkpoint_path):
    os.makedirs(checkpoint_path)

callback_checkpoint = callbacks.ModelCheckpoint(filepath=checkpoint_path + 'best_bert_weights.h5', 
                                                monitor='val_sparse_categorical_accuracy',
                                                save_best_only=True, 
                                                save_weights_only = True, 
                                                verbose=1) 
                                                
# Early-stopping for preventing the overfitting
callback_earlystop = callbacks.EarlyStopping(monitor='val_sparse_categorical_accuracy', 
                                             min_delta=0.0001, 
                                             patience=5) 

Drive already mounted at /gdrive; to attempt to forcibly remount, call drive.mount("/gdrive", force_remount=True).


In [ ]:
history = model.fit(train_inputs, train_labels, validation_split=0.2,
                    epochs=10, batch_size=200,
                    verbose=1,
                    callbacks=[callback_checkpoint, callback_earlystop])

Epoch 1/10


INFO:absl:TPU has inputs with dynamic shapes: [<tf.Tensor 'Const:0' shape=() dtype=int32>, <tf.Tensor 'cond/Identity:0' shape=(None, 300) dtype=int64>, <tf.Tensor 'cond/Identity_8:0' shape=(None, 300) dtype=int64>, <tf.Tensor 'cond/Identity_16:0' shape=(None, 300) dtype=int64>, <tf.Tensor 'cond/Identity_24:0' shape=(None,) dtype=int64>]
INFO:absl:TPU has inputs with dynamic shapes: [<tf.Tensor 'Const:0' shape=() dtype=int32>, <tf.Tensor 'cond/Identity:0' shape=(None, 300) dtype=int64>, <tf.Tensor 'cond/Identity_8:0' shape=(None, 300) dtype=int64>, <tf.Tensor 'cond/Identity_16:0' shape=(None, 300) dtype=int64>, <tf.Tensor 'cond/Identity_24:0' shape=(None,) dtype=int64>]


195/195 [==============================] - ETA: 0s - loss: 1.9353 - sparse_categorical_accuracy: 0.1720

INFO:absl:TPU has inputs with dynamic shapes: [<tf.Tensor 'Const:0' shape=() dtype=int32>, <tf.Tensor 'cond/Identity:0' shape=(None, 300) dtype=int64>, <tf.Tensor 'cond/Identity_8:0' shape=(None, 300) dtype=int64>, <tf.Tensor 'cond/Identity_16:0' shape=(None, 300) dtype=int64>, <tf.Tensor 'cond/Identity_24:0' shape=(None,) dtype=int64>]



Epoch 1: val_sparse_categorical_accuracy improved from -inf to 0.22178, saving model to /gdrive/MyDrive/final/colab_data/saved_models/best_bert_weights.h5
195/195 [==============================] - 284s 882ms/step - loss: 1.9353 - sparse_categorical_accuracy: 0.1720 - val_loss: 1.9006 - val_sparse_categorical_accuracy: 0.2218
Epoch 2/10
195/195 [==============================] - ETA: 0s - loss: 1.8288 - sparse_categorical_accuracy: 0.2942
Epoch 2: val_sparse_categorical_accuracy improved from 0.22178 to 0.39101, saving model to /gdrive/MyDrive/final/colab_data/saved_models/best_bert_weights.h5
195/195 [==============================] - 95s 486ms/step - loss: 1.8288 - sparse_categorical_accuracy: 0.2942 - val_loss: 1.6574 - val_sparse_categorical_accuracy: 0.3910
Epoch 3/10
195/195 [==============================] - ETA: 0s - loss: 1.5622 - sparse_categorical_accuracy: 0.4208
Epoch 3: val_sparse_categorical_accuracy improved from 0.39101 to 0.47475, saving model to /gdrive/MyDrive/fina

# Evaluate

In [ ]:
SEQ_LEN = 300 # 최대 token 개수 이상의 값으로 임의로 설정

token_ids =[]
token_masks =[]
token_segments =[]

test_labels = []


for idx in tqdm(range(len(test_x))):

    test_sentence = test_x.iloc[idx]
    
    # 특수문자 제거
    cleaned_sentence = re.sub("[^\s0-9a-zA-Zㄱ-ㅎㅏ-ㅣ가-힣]", "", test_sentence) 
    
    # Tokenizing / Tokens to sequence numbers / Padding
    encoded_dict = tokenizer.encode_plus(text=cleaned_sentence,
                                         padding='max_length', 
                                         truncation=True,
                                         max_length=SEQ_LEN)
    
    token_ids.append(encoded_dict['input_ids']) # tokens_tensor
    token_masks.append(encoded_dict['attention_mask']) # masks_tensor
    token_segments.append(encoded_dict['token_type_ids']) # segments_tensor

    test_labels.append(test_y.iloc[idx])


test_inputs = (np.array(token_ids), np.array(token_masks), np.array(token_segments))
test_labels = np.array(test_labels)

100%|██████████| 20880/20880 [00:05<00:00, 4022.71it/s]


In [ ]:
model.load_weights(filepath=checkpoint_path + 'best_bert_weights.h5') # Load the best model's weights from checkpoint file

preds = model.predict(test_inputs)
preds = tf.argmax(preds, axis=1)

print("Accuracy: ",accuracy_score(preds, test_labels))

INFO:absl:TPU has inputs with dynamic shapes: [<tf.Tensor 'Const:0' shape=() dtype=int32>, <tf.Tensor 'cond/Identity:0' shape=(None, 300) dtype=int64>, <tf.Tensor 'cond/Identity_8:0' shape=(None, 300) dtype=int64>, <tf.Tensor 'cond/Identity_16:0' shape=(None, 300) dtype=int64>]


Accuracy:  0.5846743295019157


In [ ]:
from sklearn.metrics import precision_score , recall_score , confusion_matrix, classification_report

#target_names = ['Neutral','Positive','Negative']
target_names = ['angry','neutral','surprise',"happiness","sadness","disgust","fear"]

precision = precision_score(test_labels, preds,average= "macro")
recall = recall_score(test_labels, preds,average= "macro")

print("< Confusion Matrix >\n\n",confusion_matrix(test_labels, preds))
print("\n")
print("< Classification Report >\n\n",classification_report(test_labels, preds, target_names=target_names))

< Confusion Matrix >

 [[1815  550  344   62  200  576   83]
 [ 259 2034  580  199  255  101  111]
 [ 173  514 1930  155  142  177  232]
 [  36  257  220 2443  169   76   28]
 [ 137  343  167  100 1687   75  310]
 [ 517  131  242   69  143 1080  106]
 [  70  144  248   32  258   81 1219]]


< Classification Report >

               precision    recall  f1-score   support

       angry       0.60      0.50      0.55      3630
     neutral       0.51      0.57      0.54      3539
    surprise       0.52      0.58      0.55      3323
   happiness       0.80      0.76      0.78      3229
     sadness       0.59      0.60      0.59      2819
     disgust       0.50      0.47      0.48      2288
        fear       0.58      0.59      0.59      2052

    accuracy                           0.58     20880
   macro avg       0.59      0.58      0.58     20880
weighted avg       0.59      0.58      0.59     20880



# Save Model

In [ ]:
from google.colab import drive
drive.mount('/gdrive')


data_path = '/gdrive/MyDrive/final/colab_data/temp_data/' 

if not os.path.exists(data_path): 
    os.makedirs(data_path)


with open(data_path + 'model_BERTfunction_v1.pkl', 'wb') as f:
    pickle.dump(dill.dumps(create_model), f) # use dill to pickle a function (https://j.mp/3CeSIzP & https://j.mp/3AaXxYW)

with open(data_path + 'tokenizer-bert.pkl', 'wb') as f:
    pickle.dump(tokenizer, f)     

Drive already mounted at /gdrive; to attempt to forcibly remount, call drive.mount("/gdrive", force_remount=True).


Load

In [ ]:
!pip install transformers==4.8.2
!pip install tensorflow_addons

import pandas as pd
import numpy as np

import re
import os
import pickle 
import dill # for saving a function as a file
import logging # for changing the tf's logging level
from IPython.display import clear_output 

import tensorflow as tf
import tensorflow_addons as tfa
from tensorflow.keras import layers, initializers, losses, optimizers, metrics 

import transformers
from transformers import TFBertModel 

# 이번 실습에서 추가되었습니다
!pip install sentencepiece==0.1.96
import sentencepiece as spm 
!git clone https://github.com/monologg/KoBERT-Transformers.git 
!mv KoBERT-Transformers/kobert_transformers/tokenization_kobert.py /content 
from tokenization_kobert import KoBertTokenizer 

# Tensorflow logging level 변경 
tf.get_logger().setLevel(logging.ERROR)

# clear the output after the installation
clear_output() 

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [ ]:
# 1) Load the Model-builder function
with open("/content/drive/MyDrive/final/colab_data/temp_data/model_BERTfunction_v1.pkl", 'rb') as f: # 이번 실습에서 변경되었습니다
    create_model = dill.loads(pickle.load(f)) # use dill to pickle a python function

In [ ]:
# 2) Load the Bert-tokenizer 
with open("/content/drive/MyDrive/final/colab_data/temp_data/tokenizer-bert.pkl", 'rb') as f:
    tokenizer = pickle.load(f) 

In [ ]:
resolver = tf.distribute.cluster_resolver.TPUClusterResolver(tpu='grpc://' + os.environ['COLAB_TPU_ADDR'])
tf.config.experimental_connect_to_cluster(resolver)
tf.tpu.experimental.initialize_tpu_system(resolver)
strategy = tf.distribute.TPUStrategy(resolver) # Obsolete : tf.distribute.experimental.TPUStrategy()

with strategy.scope(): 
    model = create_model(max_length=300) 

In [ ]:
checkpoint_path = '/content/drive/MyDrive/final/colab_data/saved_models/'
model.load_weights(filepath=checkpoint_path + 'best_bert_weights.h5')

In [ ]:
def predict_sentiment(sentence, tokenizer, model):
    
    SEQ_LEN = 300 

    # Tokenizing / Tokens to sequence numbers / Padding
    encoded_dict = tokenizer.encode_plus(text=re.sub("[^\s0-9a-zA-Zㄱ-ㅎㅏ-ㅣ가-힣]", "", sentence),
                                         padding='max_length', 
                                         truncation = True,
                                         max_length=SEQ_LEN) 
    
    token_ids = np.array(encoded_dict['input_ids']).reshape(1, -1) 
    token_masks = np.array(encoded_dict['attention_mask']).reshape(1, -1)
    token_segments = np.array(encoded_dict['token_type_ids']).reshape(1, -1)
    
    new_inputs = (token_ids, token_masks, token_segments)

    # Prediction
    prediction = model.predict(new_inputs)
    predicted_probability = np.round(np.max(prediction) * 100, 2) 
    # "분노":0,"중립":1, "놀람":2, "행복":3, "슬픔":4, "혐오":5,"공포":6 
    predicted_class = ["분노",'중립','놀람', '행복',"슬픔","혐오","공포"][np.argmax(prediction, axis=1)[0]] 
    
    print("{}% 확률로 {} 리뷰입니다.".format(predicted_probability, predicted_class))

In [ ]:
song="이윽고 내가 한눈에너를 알아봤을 때모든 건 분명 달라지고 있었어내 세상은 널 알기 전과 후로 나뉘어니가 숨 쉬면 따스한 바람이 불어와니가 웃으면 눈부신 햇살이 비춰거기 있어줘서 그게 너라서가끔 내 어깨에 가만히 기대주어서나는 있잖아 정말 빈틈없이 행복해너를 따라서 시간은 흐르고 멈춰물끄러미 너를 들여다 보곤 해그것 말고는 아무것도 할 수 없어서너의 모든 순간 그게나였으면 좋겠다생각만 해도 가슴이 차올라나는 온통 너로보고 있으면 왠지 꿈처럼 아득한 것몇 광년 동안 날 향해 날아온 별빛 또 지금의 너거기 있어줘서 그게 너라서가끔 나에게 조용하게 안겨주어서나는 있잖아 정말 남김없이 고마워너를 따라서 시간은 흐르고 멈춰물끄러미 너를 들여다보곤 해너를 보는 게 나에게는 사랑이니까너의 모든 순간 그게나였으면 좋겠다생각만 해도 가슴이 차올라나는 온통 너로니 모든 순간 나였으면"

In [ ]:
song1="네가 없이 웃을 수 있을까생각만 해도 눈물이나힘든 시간 날 지켜준 사람이제는 내가 그댈 지킬 테니너의 품은 항상 따뜻했어고단했던 나의 하루에유일한 휴식처나는 너 하나로 충분해긴 말 안 해도 눈빛으로 다 아니깐한 송이의 꽃이 피고 지는모든 날 모든 순간 함께해햇살처럼 빛나고 있었지나를 보는 네 눈빛은꿈이라고 해도 좋을 만큼그 모든 순간은 눈부셨다불안했던 나의 고된 삶에한줄기 빛처럼 다가와날 웃게 해준 너나는 너 하나로 충분해긴 말 안 해도 눈빛으로 다 아니깐한 송이의 꽃이 피고 지는모든 날 모든 순간 함께해알 수 없는 미래지만네 품속에 있는 지금 순간 순간이영원 했으면 해갈게 바람이 좋은 날에햇살 눈부신 어떤 날에 너에게로처음 내게 왔던 그날처럼모든 날 모든 순간 함께해"

In [ ]:
predict_sentiment(song, tokenizer, model)

NameError: ignored

In [ ]:
predict_sentiment(song1, tokenizer, model)

82.97% 확률로 슬픔 리뷰입니다.


In [ ]:
song2="일부러 몇 발자국 물러나내가 없이 혼자 걷는 널 바라본다옆자리 허전한 너의 풍경흑백 거리 가운데 넌 뒤돌아본다그때 알게 되었어난 널 떠날 수 없단 걸우리 사이에 그 어떤 힘든 일도이별보단 버틸 수 있는 것들이었죠어떻게 이별까지 사랑"

In [ ]:
predict_sentiment(song2, tokenizer, model)

88.51% 확률로 슬픔 리뷰입니다.


In [ ]:
song3="너는 참 못됐다나 없이도 잘 지내더라 언제쯤 나도 널 잊을 수 있을까 눈을 감아도 눈물이 흐르고 어딜 가도 너만 보여 어느새 니가 없는긴 하루가 지나간다 다른 사람을 또 만나봐도 니가 아님 안 되겠어 울다가 또 웃다가 미친 것처럼 또 보고 싶다 상처 같은 널 잊어보려고 아무리 애를 써도너만 보고 싶다 니가 없인 아무것도 못 해 니가 없는 나는 아무것도 아냐 나도 참 못됐다 자꾸만 또 힘이 들더라 예전처럼 돌아갈 수가 있을까 눈을 감아도 니가 떠오르고 어딜 가도 너만 보여 자주 걷던 그 길 끝 저 너머 그댄 보일까요 다른 사람을 또 만나봐도 니가 아님 안 되겠어 울다가 또 웃다가 미친 것처럼 또 보고 싶다 상처 같은 널 잊어보려고 아무리 애를 써도 너만 보고 싶다니가"

In [ ]:
predict_sentiment(song3, tokenizer, model)

82.09% 확률로 슬픔 리뷰입니다.


In [ ]:
song4="오늘도 본을 떠 원효대사 해골물오 월 로제 미카사 아커만Don't worry 돈과 빛 재산 해결 못해정월대보름에 늑대야 에구머니나원효대사 오면 절이 엎어지고현역 대상 오 불합격추억팔이 은폐엄폐어우 연애는 나 못 해저기 오빠 또 해줘저녁에 소고기 쏴버려 엎어 지갑래원이는 원효대사 now잃어버린 대사관엔루머에 가린 패싸움 달인이름 모를 그 사나이피곤해 방콕해 직원 해방100원에 박혀있는 뜨거운 파편비구름 밖 지구 네 바퀴비굴의 파견 미군의 방패보아뱀 닮아버린 반 페르시부합해 루시퍼 베드신발포해 리스폰페르시아 완패를 시켜죽은 애들과 붉은 횃불빅원의 품은 포근해 woo량주 먹고 토해 알고 보니 해골물담주목금토일 like 거머리의 그물설총 사회적 파장 가져와서울 종각에 프란체스카Guess what카드 보안 필수 카르마 티리비두 팀이 비슷한 순간산송장 빌의 버저 비트스필버그 링컨 휘파람 비트 틀고NBA 번호 뒤에 달아부리나케 달아나파란 하늘 나무늘보나문희 호박 고구마필트오버 블리츠 how much겨울에 얼어버린 미토콘드리아아랍에미레이트 항공부익부 빈익빈미필이 부린 객기Fred Perry 구입뿔뿔이 대피구름 위를 걸으면 VIP그림을 그려봐 머피의 법칙또 본을 떠 원효대사 해골물오 월 로제 미카사 아커만Don't worry 돈과 빛재산 해결 못해정월대보름에 늑대야 에구머니나원효대사 오면 절이 엎어지고현역 대상 오 불합격추억팔이 은폐엄폐어우 연애는 나 못 해저기 오빠 또 해줘저녁에 소고기 쏴버려 엎어 지갑아빠 저금통 500원짜리누가 자꾸 털어 암행어사 필요해 치고 박고 싸워지구본이 손에 느껴져그토록 설레발 애써 네이버뒤져봐도 안 나오는 헛된 바램수원대 입구 앞에 벌어대 guap허파에 바람 들어가서 부활해어차피 떠나갈 새끼들 보임충고 때려 넣고 이어폰 꽂고 poem그대로 보여줘카톡으로 ㅋㅋ that point뻔하지 카테고리 똥글에 부워래원인 반칙 꼬라박지 rhyme shit영원히 갇힌 네 힙합이 나의 간식"

In [ ]:
predict_sentiment(song4, tokenizer, model)

58.89% 확률로 분노 리뷰입니다.


영어 50%이상 제거, 띄어쓰기 처리


In [ ]:
!pip install konlpy==0.5.2

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


In [ ]:
import pandas as pd 

from konlpy import tag
from konlpy.corpus import kolaw
from konlpy.utils import pprint 

!pip install git+https://github.com/ssut/py-hanspell.git

from hanspell import spell_checker

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
  Cloning https://github.com/ssut/py-hanspell.git to /tmp/pip-req-build-58a1nn7n
  Running command git clone -q https://github.com/ssut/py-hanspell.git /tmp/pip-req-build-58a1nn7n


In [ ]:
import platform

#운영체제에 따라 mecab설치 방법이 다름.
if platform.system() == "Windows":
    try:
        from eunjeon import Mecab
        
    except:
        print("please install eunjeon module")
else:  # Ubuntu일 경우
  try:
    from konlpy.tag import Mecab
  except:
    print("please install Mecab")

In [ ]:
df_balad = pd.read_excel('/content/drive/MyDrive/final (1)/data_song_scraping/balad_500songs.xlsx')
df_dance = pd.read_excel("/content/drive/MyDrive/final (1)/data_song_scraping/dance_500songs.xlsx")
df_fork_blues = pd.read_excel("/content/drive/MyDrive/final (1)/data_song_scraping/fork_blues_500songs.xlsx")
df_indi = pd.read_excel("/content/drive/MyDrive/final (1)/data_song_scraping/indi_500songs.xlsx")
df_r_b = pd.read_excel("/content/drive/MyDrive/final (1)/data_song_scraping/r&b_500songs.xlsx")
df_rap_hiphop = pd.read_excel("/content/drive/MyDrive/final (1)/data_song_scraping/RapHipHop_500songs.xlsx")
df_rock_metal = pd.read_excel("/content/drive/MyDrive/final (1)/data_song_scraping/rock_metal_500songs.xlsx") 
df_trot_hiphop = pd.read_excel("/content/drive/MyDrive/final (1)/data_song_scraping/trot_500songs.xlsx")

In [ ]:
df_allsongs = pd.concat([df_balad, df_dance, df_fork_blues, df_indi, df_r_b, df_rap_hiphop, df_rock_metal, df_trot_hiphop])

In [ ]:
df_allsongs

Title         Artist        Date       Genre  \
0        사랑인가 봐           멜로망스  2022.02.18  발라드, 국내드라마   
1        나의 X에게             경서  2022.04.24         발라드   
2          취중고백     김민석 (멜로망스)  2021.12.19         발라드   
3     사랑은 늘 도망가            임영웅  2021.10.11  발라드, 국내드라마   
4        듣고 싶을까  MSG워너비(M.O.M)  2022.02.26         발라드   
..          ...            ...         ...         ...   
495         만약에            조항조  2020.07.31    성인가요/트로트   
496     용두산 엘레지            송가인  2021.03.21    성인가요/트로트   
497  단장의 미아리 고개            송가인  2020.12.26    성인가요/트로트   
498           때            조항조  2016.07.13    성인가요/트로트   
499        도찐개찐            김의영  2021.02.26    성인가요/트로트   

                                                 Lyric  
0    너와 함께 하고 싶은 일들을상상하는 게요즘 내 일상이 되고너의 즐거워하는 모습을 보...  
1    우리 다시 만날래예쁘게 빛나던모든 추억들이너무 그리워너의 품에 안길래이 밤이 새도록...  
2    뭐하고 있었니 늦었지만잠시 나올래너의 집 골목에 있는놀이터에 앉아 있어친구들 만나서...  
3    눈물이 난다 이 길을 걸으면그 사람 손길이 자꾸 생각이 난다붙잡지 못하고 가슴만 떨...  
4    우리 함께 듣던 그 노랠 듣고 싶을까듣고 나서 잠시 날 생각은 할까아주 혹시라도 넌...  
..                                                 ...  
495  만약에 당신이 그 누구와 사랑에 빠지면 그 사랑을 위해서 무얼할 수 있나 텅빈세상 ...  
496  용두산아 용두산아너만은 변치 말자한 발 올려 맹세하고두 발 디뎌 언약하던한 계단 두...  
497  미아리 눈물고개임이 넘던 이별 고개화약 연기 앞을 가려눈 못 뜨고 헤매일 때당신은 ...  
498  낮춰야 할 때는 낮춰야하고 물러나야 할 때는 물러나야지 오르고 오르면 끝이 있듯이 ...  
499  사랑하다 헤어지고 좋아하다 미워하고 돌고도는 세상살이가 돌고도는 인생살이가 왜이리 ...  

[4000 rows x 5 columns]

In [ ]:
df_allsongs.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 4000 entries, 0 to 499
Data columns (total 5 columns):
 #   Column  Non-Null Count  Dtype 
---  ------  --------------  ----- 
 0   Title   4000 non-null   object
 1   Artist  4000 non-null   object
 2   Date    4000 non-null   object
 3   Genre   4000 non-null   object
 4   Lyric   4000 non-null   object
dtypes: object(5)
memory usage: 187.5+ KB


In [ ]:
df_allsongs['Lyric'].nunique() 

3551

In [ ]:
df_allsongs.drop_duplicates(subset = ['Lyric'], inplace = True)
len(df_allsongs)

3551

In [ ]:
def drop_if_eng(df): 
    df['one_string'] = df['Lyric'].str.join(" ") 
    mecab = Mecab() 
    for i in df.one_string:
        sents = mecab.pos(i) 
        n = 0 # n: SL(외국어)태그의 숫자
        result = []
        for word in sents:
            if word[1] == 'SL': # SL: Mecab에서 외국어 의미
                n += 1
        if n > (len(sents)//2): # 50% 넘으면 제거 
            df = df[df.one_string != i] 
            # print(len(df)) 
    return df

In [ ]:
!curl -s https://raw.githubusercontent.com/teddylee777/machine-learning/master/99-Misc/01-Colab/mecab-colab.sh | bash

--2022-05-24 15:47:37--  https://www.dropbox.com/s/9xls0tgtf3edgns/mecab-0.996-ko-0.9.2.tar.gz?dl=1
Resolving www.dropbox.com (www.dropbox.com)... 162.125.9.18, 2620:100:601b:18::a27d:812
Connecting to www.dropbox.com (www.dropbox.com)|162.125.9.18|:443... connected.
HTTP request sent, awaiting response... 301 Moved Permanently
Location: /s/dl/9xls0tgtf3edgns/mecab-0.996-ko-0.9.2.tar.gz [following]
--2022-05-24 15:47:37--  https://www.dropbox.com/s/dl/9xls0tgtf3edgns/mecab-0.996-ko-0.9.2.tar.gz
Reusing existing connection to www.dropbox.com:443.
HTTP request sent, awaiting response... 302 Found
Location: https://uc267ee6ed0558acb60a5c70ff8f.dl.dropboxusercontent.com/cd/0/get/Bl5AevcxAUDft85dhQ_AlI7o4YkrlKvWaUvDvOsWDN8YBh2Md-WurBZlFPdT6FiUx44BHRoECrxqVPoFfPaDKnycnHOajc2q2OWhPolYYcY6E05DhWcWItscS_65kCdYzsW26cJMkLOdSJ10GkaVjeKEKgW9xQ30ZpXBoSXnQjXd4zBWH_0XC5L4gPTS2Dp4_t0/file?dl=1# [following]
--2022-05-24 15:47:37--  https://uc267ee6ed0558acb60a5c70ff8f.dl.dropboxusercontent.com/cd/0/get/

In [ ]:
from konlpy.tag import Mecab
!git clone https://github.com/SOMJANG/Mecab-ko-for-Google-Colab.git
%cd Mecab-ko-for-Google-Colab/
!bash install_mecab-ko_on_colab190912.sh

Cloning into 'Mecab-ko-for-Google-Colab'...
remote: Enumerating objects: 115, done.
remote: Counting objects: 100% (24/24), done.
remote: Compressing objects: 100% (20/20), done.
remote: Total 115 (delta 11), reused 10 (delta 3), pack-reused 91
Receiving objects: 100% (115/115), 1.27 MiB | 8.73 MiB/s, done.
Resolving deltas: 100% (50/50), done.
/content/Mecab-ko-for-Google-Colab
Installing konlpy.....
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
Done
Installing mecab-0.996-ko-0.9.2.tar.gz.....
from https://bitbucket.org/eunjeon/mecab-ko/downloads/mecab-0.996-ko-0.9.2.tar.gz
--2022-05-24 16:11:09--  https://bitbucket.org/eunjeon/mecab-ko/downloads/mecab-0.996-ko-0.9.2.tar.gz
Resolving bitbucket.org (bitbucket.org)... 104.192.141.1, 2406:da00:ff00::22e9:9f55, 2406:da00:ff00::22cd:e0db, ...
Connecting to bitbucket.org (bitbucket.org)|104.192.141.1|:443... connected.
HTTP request sent, awaiting response... 302 Found
Location: https://bb

In [ ]:
from konlpy.tag import Okt, Mecab

mecab = Mecab()

In [ ]:
df_saved = drop_if_eng(df_allsongs)

In [ ]:
df_woeng = df_saved[['Title', 'Artist', 'Date', 'Genre', 'one_string']] # dataframe without english
df_woeng.one_string = df_woeng.one_string.str.replace(" ", '')
df_woeng

/usr/local/lib/python3.7/dist-packages/pandas/core/generic.py:5516: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self[name] = value


Title         Artist        Date       Genre  \
0        사랑인가 봐           멜로망스  2022.02.18  발라드, 국내드라마   
1        나의 X에게             경서  2022.04.24         발라드   
2          취중고백     김민석 (멜로망스)  2021.12.19         발라드   
3     사랑은 늘 도망가            임영웅  2021.10.11  발라드, 국내드라마   
4        듣고 싶을까  MSG워너비(M.O.M)  2022.02.26         발라드   
..          ...            ...         ...         ...   
495         만약에            조항조  2020.07.31    성인가요/트로트   
496     용두산 엘레지            송가인  2021.03.21    성인가요/트로트   
497  단장의 미아리 고개            송가인  2020.12.26    성인가요/트로트   
498           때            조항조  2016.07.13    성인가요/트로트   
499        도찐개찐            김의영  2021.02.26    성인가요/트로트   

                                            one_string  
0    너와함께하고싶은일들을상상하는게요즘내일상이되고너의즐거워하는모습을보고있으면자연스레따라웃...  
1    우리다시만날래예쁘게빛나던모든추억들이너무그리워너의품에안길래이밤이새도록네게말할거야너를좋...  
2    뭐하고있었니늦었지만잠시나올래너의집골목에있는놀이터에앉아있어친구들만나서오랜만에술을좀했는...  
3    눈물이난다이길을걸으면그사람손길이자꾸생각이난다붙잡지못하고가슴만떨었지내아름답던사람아사랑...  
4    우리함께듣던그노랠듣고싶을까듣고나서잠시날생각은할까아주혹시라도넌내가보고싶을까난왜니목소리...  
..                                                 ...  
495  만약에당신이그누구와사랑에빠지면그사랑을위해서무얼할수있나텅빈세상살아가는이유가만약에너라면...  
496  용두산아용두산아너만은변치말자한발올려맹세하고두발디뎌언약하던한계단두계단일백구십사계단에사...  
497  미아리눈물고개임이넘던이별고개화약연기앞을가려눈못뜨고헤매일때당신은철사줄로두손꽁꽁묶인채로...  
498  낮춰야할때는낮춰야하고물러나야할때는물러나야지오르고오르면끝이있듯이내려올때도끝이있다네막막...  
499  사랑하다헤어지고좋아하다미워하고돌고도는세상살이가돌고도는인생살이가왜이리힘이들더냐너나나나...  

[2988 rows x 5 columns]

In [ ]:
from hanspell import spell_checker 

test_nospace = df_woeng.one_string.iloc[13]
print(type(test_nospace))
spelled_test = spell_checker.check(test_nospace) 

hanspell_test = spelled_test.checked
print(hanspell_test)

<class 'str'>



In [ ]:
test_nospace = df_woeng.one_string.iloc[29]
print(type(test_nospace))
spelled_test = spell_checker.check(test_nospace) 

hanspell_test = spelled_test.checked
print(hanspell_test)

<class 'str'>
꿈처럼 지나간 시간 나는 무얼 찾고 싶었나 지도도 없이 걸어온 삶을 후회하진 않으리 떠난 어제는 떠날 오늘로 남겨지기도 하지 나의 친구여 나의 형제여 내 이름 불러 수오미 안 하다 나의 인생아 앞만 보며 살아왔구나 찬란한 순간이여 영원하라 내일은 처음 가는 길 언제나처럼 또 두려워 버들강아지 활짝 웃는 날 후회하지 않으리 비가 내리면 노래하리 눈이 내려도 좋아나의 친구여 나의 형제여 내 이름 불러 수오미 안 하다 나의 인생아 앞만 보며 살아왔구나 찬란한 순간이여 영원하라 영원한 순간이여 찬란하라


In [ ]:
df_woeng['one_string'].describe()

count                                                  2988
unique                                                 2922
top       미련없다그말이진정인가요냉정했던그마음이진정인가요바닷가를거닐며수놓았던그추억잊을수가있을까...
freq                                                      3
Name: one_string, dtype: object

In [ ]:
df_woeng["one_string_check"]="x"

In [ ]:
for row, col in df_woeng.iterrows():
  print(type(df_woeng.iloc[row]["one_string"]))
  spell_test=spell_checker.check(df_woeng.iloc[row]["one_string"])
  print(spell_test)
  # df_woeng.iloc[row]["one_string_check"]=spell_test.checked
# df_weong["one_string_check"]=df_woeng['one_string'].apply(lambda x : spell_checker.check(x).checked) 

<class 'str'>
Checked(result=True, original='너와함께하고싶은일들을상상하는게요즘내일상이되고너의즐거워하는모습을보고있으면자연스레따라웃고있는걸너의행동에설레어하고뒤척이다가지새운밤이많아지는데이건누가봐도사랑일텐데종일함께면질릴텐데나돌아서도온통너인건아무래도사랑인가봐점점너와하고싶은일들생각하면서하룰보낸날이많아지는데이건누가봐도사랑일텐데종일함께면질릴텐데나돌아서도온통너인건아무래도사랑인가봐너의행복해하는모습을보고있으면나도모르게따라웃는데이정도면알아줄만하잖아너도용기낼만하잖아나만이런게아니라면우리만나볼만하잖아아무래도사랑인가봐', checked='너와 함께하고 싶은 일들을 상상하는 게 요 즘 내 일상이 되고 너의 즐거워하는 모습을 보고 있으면 자연스레 따라 웃고 있는 걸 너의 행동에 설레고 뒤척이다가 지새운 밤이 많아지는데 이건 누가 봐도 사랑일 텐데 종일 함께 면 질릴 텐데라 돌아서도 온통 너인 건 아무래도 사랑인가 봐 점점 너와 하고 싶은 일들 생각하면서 하룰 보낸 날이 많아지는데 이건 누가 봐도 사랑일 텐데 종일 함께 면 질릴 텐데라 돌아서도 온통 너인 건 아무래도 사랑인가 봐 너의 행복해하는 모습을 보고 있으면 나도 모르게 따라 웃는데 이 정도면 알아줄 만하잖아 너도 용기 낼 만하잖아 나만 이런 게 아니라면 우리 만나볼 만하잖아 아무래도 사랑인가 봐', errors=1, words=OrderedDict([('너와', 4), ('함께하고', 4), ('싶은', 4), ('일들을', 4), ('상상하는', 4), ('게', 4), ('요', 4), ('즘', 4), ('내', 4), ('일상이', 4), ('되고', 4), ('너의', 4), ('즐거워하는', 4), ('모습을', 4), ('보고', 4), ('있으면', 4), ('자연스레', 4), ('따라', 4), ('웃고', 4), ('있는', 4), ('걸', 4), ('행동에', 4), ('설레고', 4), ('뒤척이다가', 4), ('지새운', 4), ('밤이', 4), ('많아지는데', 4),

JSONDecodeError: ignored

In [ ]:
df_woeng.head(30)

Title         Artist        Date  \
0                                  사랑인가 봐           멜로망스  2022.02.18   
1                                  나의 X에게             경서  2022.04.24   
2                                    취중고백     김민석 (멜로망스)  2021.12.19   
3                               사랑은 늘 도망가            임영웅  2021.10.11   
4                                  듣고 싶을까  MSG워너비(M.O.M)  2022.02.26   
5                           다정히 내 이름을 부르면           경서예지  2021.05.19   
6                                우리들의 블루스            임영웅  2022.04.17   
7                                 언제나 사랑해    케이시 (Kassy)  2022.02.07   
8                             다시 만날 수 있을까            임영웅  2022.05.02   
9                                     드라마            아이유  2021.12.29   
10                               너의 모든 순간            성시경  2014.02.12   
11                                내가 아니라도             주호  2022.03.25   
12                                내 손을 잡아            아이유  2011.05.25   
13                                  호랑수월가             탑현  2022.01.15   
14                                 바라만 본다  MSG워너비(M.O.M)  2021.06.26   
15                       눈이 오잖아(Feat.헤이즈)            이무진  2021.12.03   
16                          밤하늘의 별을(2020)             경서  2020.11.14   
17                                     고백           멜로망스  2021.08.29   
19                                   사랑인걸            한동근  2022.03.13   
20  모든 날, 모든 순간 (Every day, Every Moment)             폴킴  2018.03.20   
21           너, 너 (N번째 연애 X 휘인 (Whee In))   휘인 (Whee In)  2022.02.13   
22                                    팡파레            다비치  2022.05.16   
23              어떻게 이별까지 사랑하겠어, 널 사랑하는 거지      AKMU (악뮤)  2019.09.25   
24                                   어제처럼             폴킴  2022.02.27   
25                                     초대           멜로망스  2022.05.03   
26                                     서랍           10CM  2021.12.07   
27                                    아버지            임영웅  2022.05.02   
28                             너의 번호를 누르고            김나영  2022.04.12   
29                                 미친 것처럼          V.O.S  2022.05.15   
31                                   인생찬가            임영웅  2022.05.02   

         Genre                                         one_string  \
0   발라드, 국내드라마  너와함께하고싶은일들을상상하는게요즘내일상이되고너의즐거워하는모습을보고있으면자연스레따라웃...   
1          발라드  우리다시만날래예쁘게빛나던모든추억들이너무그리워너의품에안길래이밤이새도록네게말할거야너를좋...   
2          발라드  뭐하고있었니늦었지만잠시나올래너의집골목에있는놀이터에앉아있어친구들만나서오랜만에술을좀했는...   
3   발라드, 국내드라마  눈물이난다이길을걸으면그사람손길이자꾸생각이난다붙잡지못하고가슴만떨었지내아름답던사람아사랑...   
4          발라드  우리함께듣던그노랠듣고싶을까듣고나서잠시날생각은할까아주혹시라도넌내가보고싶을까난왜니목소리...   
5          발라드  끝없이별빛이내리던밤기분좋은바람이두빰을스치고새벽바다한곳을보는아름다운너와나그림을그려갔어...   
6          발라드  잊지는말아요함께했던날들눈물이날때면그대뒤를돌아보면돼요아프지말아요쓸쓸한마음에힘든일이참많...   
7          발라드  둘이손잡고걸을때마주보며또웃을때사랑한다말하지않아도알아널만나러가는길에내입가에늘환한미소만...   
8          발라드  너를위해해줄것이하나없어서보낼수밖에없었고네가없이사는법을알지못해서순간순간을울었다후회로가...   
9          발라드  나도한때는그이의손을잡고내가온세상주인공이된듯꽃송이의꽃잎하나하나까지모두날위해피어났지올림...   
10  발라드, 국내드라마  이윽고내가한눈에너를알아봤을때모든건분명달라지고있었어내세상은널알기전과후로나뉘어니가숨쉬면...   
11         발라드  사랑이었다별거없던내하루에빛이돼준단한사람나보다나를더아껴주던너를그땐왜몰랐을까행복이었다다...   
12  발라드, 국내드라마  느낌이오잖아\n떨리고있잖아\n언제까지눈치만볼거니\n네맘을말해봐\n딴청피우지말란말이야...   
13         발라드  흐르는저하늘을물어채는범처럼태산에날아들어숨어드는새처럼동산을뛰고뛰어가는강아지처럼온산에풍...   
14         발라드  내가너라면다알아볼텐데널위할사람찾아낼텐데지난오랜시간너의그곁을지켜온나라는걸내가너였다면참...   
15         발라드  한달좀덜된기억들주머니에넣은채걷고있어몇시간을혹시몰라네가좋아했던코트를입은채나온번화가그때...   
16         발라드  밤하늘의별을따서너에게줄래너는내가사랑하니까더소중하니까오직너아니면안된다고외치고싶어그저내...   
17   발라드, 인디음악  달이차고내마음도차고이대로담아두기엔너무안타까워너를향해가는데달은내게오라손짓하고귓속에얘길...   
19         발라드  하루가가는소릴들어너없는세상속에달이저물고해가뜨는서러움한날도한시도못살것같더니그저이렇게그...   
20  발라드, 국내드라마  네가없이웃을수있을까생각만해도눈물이나힘든시간날지켜준사람이제는내가그댈지킬테니너의품은항상...   
21         발라드  하루종일집에누워서전화기만보고있잖아내머릿속은네생각들로만짜여져있어날찾지않아도좋아하지않아...   
22         발라드  코끝을간지럽히는살랑부는바람이눈감으면어디든네곁에데려가주길어느새내맘이춤을추네한없이예쁜날...   
23         발라드  일부러몇발자국물러나내가없이혼자걷는널바라본다옆자리허전한너의풍경흑백거리가운데넌뒤돌아본다...   
24         발라드  TrustthewarmthinsideCanyoufeelmylovealive어제처럼오...   
25   발라드, 인디음악  네가떠올라얼어붙었던내게손내밀어준널맞이할준비를해기분좋게내린햇살을보고반가운마음으로문을열...   
26  발라드, 